In [57]:
import keras
from keras.datasets import cifar10

In [58]:
(x_train, y_train), (x_test, y_test) = cifar10.load_data()
print('x_train shape:', x_train.shape)
print(x_train.shape[0], 'train samples')
print(x_test.shape[0], 'test samples')

x_train shape: (50000, 32, 32, 3)
50000 train samples
10000 test samples


In [59]:
print(x_train[0].shape)
# print(x_test[0])

(32, 32, 3)


In [60]:
import numpy as np 
import itertools
from sklearn.cluster import KMeans, MiniBatchKMeans
from sklearn.neighbors import BallTree
from sklearn.metrics import accuracy_score
import pickle
import glob
import cv2

In [61]:
def desSURF(image):
    surf = cv2.xfeatures2d.SURF_create()
    kp, des = surf.detectAndCompute(image,None)
    #draw keypoints
    #import matplotlib.pyplot as plt		
    #img2 = cv2.drawKeypoints(img,kp,None,(255,0,0),4)
    #plt.imshow(img2),plt.show()
    return kp,des

def describeORB( image):
    #An efficient alternative to SIFT or SURF
    #doc http://docs.opencv.org/3.0-beta/doc/py_tutorials/py_feature2d/py_orb/py_orb.html
    #ORB is basically a fusion of FAST keypoint detector and BRIEF descriptor 
    #with many modifications to enhance the performance
    orb=cv2.ORB_create()
    kp, des=orb.detectAndCompute(image,None)
    return kp,des

In [62]:
def getDescriptors(images) : 
    descriptors = []
    
    for image in images: 
        image = cv2.resize(image, (150, 150), interpolation=cv2.INTER_AREA)
        kp, des = desSURF(image)
        if des is not None : 
            descriptors.append(des)
            
#     descriptors = list(itertools.chain.from_iterable(descriptors))
    descriptors = np.concatenate(descriptors, axis=0)
#     descriptors = np.asarray(descriptors)
    print(descriptors)
    return descriptors

def getVLADDescriptors(images, images_lables, visualDic):
    descriptors = []
    labels = []
    
    count = 0
    for image in images : 
        image = cv2.resize(image, (150, 150), interpolation=cv2.INTER_AREA)
        kp, des = desSURF(image)
        if des is not None : 
            v = VLAD(des, visualDic)
            print(v)
            descriptors.append(v)
            labels.append(images_lables[count])
        count += 1
            
            
#     descriptors = list(itertools.chain.from_iterable(descriptors))
#     descriptors = np.asarray(descrip/tors)
    print(descriptors)  
    return descriptors, labels
    
def kMeans(training, k) : 
    est = KMeans(n_clusters = k, init = 'k-means++').fit(training)
    return est

def VLAD(X, visualDictionary) : 
    
    predictedLabels = visualDictionary.predict(X)
    centers = visualDictionary.cluster_centers_
    labels = visualDictionary.labels_
    k = visualDictionary.n_clusters
    
    m,d = X.shape
    V=np.zeros([k,d])
    #computing the differences

    # for all the clusters (visual words)
    for i in range(k):
        # if there is at least one descriptor in that cluster
        if np.sum(predictedLabels==i)>0:
            # add the diferences
            V[i]=np.sum(X[predictedLabels==i,:]-centers[i],axis=0)
    

    V = V.flatten()
    # power normalization, also called square-rooting normalization
    V = np.sign(V)*np.sqrt(np.abs(V))

    # L2 normalization

    V = V/np.sqrt(np.dot(V,V))
    return V


In [63]:
sift_des = getDescriptors(np.concatenate((x_train, x_test), axis = 0))
# visDic = kMeans(sift_des, 50)



[[-0.00109814 -0.00018986  0.00148726 ... -0.00039803  0.00389354
   0.00152968]
 [-0.00258623 -0.00100103  0.00301079 ...  0.00070776  0.00191917
   0.00119535]
 [-0.00193051 -0.0003467   0.00200452 ... -0.00018438  0.00339893
   0.00250239]
 ...
 [ 0.02049138  0.01756086  0.02092241 ... -0.02243001  0.01018546
   0.02806576]
 [-0.0063772   0.00170187  0.00690927 ... -0.00311643  0.00075985
   0.00416109]
 [-0.00071191  0.00137888  0.00447666 ...  0.00259698  0.00891337
   0.00394264]]


In [86]:
visDic = MiniBatchKMeans(init='k-means++', n_clusters=50,max_iter=1000, batch_size=1000,
                  n_init=10, max_no_improvement=10, verbose=0).fit(sift_des)

In [87]:
vlad_des, labels = getVLADDescriptors(x_train, y_train, visDic)
print ("Hola")
vlad_des_test, labels_test = getVLADDescriptors(x_test, y_test, visDic)

[-0.00473159 -0.00622607 -0.00182296 ...  0.          0.
  0.        ]
[-0.00824682  0.00600611 -0.00169854 ...  0.00863934  0.00889924
  0.00495812]
[-0.01109655 -0.00956555  0.00304855 ...  0.          0.
  0.        ]
[-0.00787039  0.00587589 -0.00409094 ...  0.          0.
  0.        ]
[-0.00558793  0.00693181 -0.00574396 ... -0.00968759 -0.0068627
  0.00483032]
[0. 0. 0. ... 0. 0. 0.]
[ 0.00662722  0.00251266  0.00141204 ... -0.00616025 -0.00570061
  0.00304541]
[-0.00649535 -0.00488531  0.00287834 ... -0.00809738  0.006685
  0.0083697 ]
[-0.00265499  0.00466571 -0.00941773 ...  0.          0.
  0.        ]
[ 0.00654297  0.00717364 -0.00578662 ...  0.00756048 -0.00659944
 -0.00418652]
[ 0.          0.          0.         ...  0.00511484  0.00885629
 -0.00395322]
[-0.00416792  0.00134698 -0.00916156 ...  0.          0.
  0.        ]
[ 0.00559504 -0.00928729 -0.00713669 ...  0.          0.
  0.        ]
[-0.00515898  0.00726674 -0.00893765 ...  0.          0.
  0.        ]
[-0.0062

[-0.00563571  0.00803408 -0.00723366 ... -0.00259771 -0.00110459
 -0.00416203]
[ 0.00403273  0.00537213 -0.00692467 ...  0.          0.
  0.        ]
[-0.01130989  0.00782703  0.00938363 ... -0.01012754  0.00266898
  0.00615162]
[ 0.00405382  0.00623633 -0.0113541  ...  0.          0.
  0.        ]
[ 0.01166893  0.00681572 -0.01497296 ...  0.          0.
  0.        ]
[ 0.01361103 -0.01683988  0.00796256 ...  0.00433521 -0.00361661
 -0.00442513]
[ 0.00374916 -0.00447726  0.00074158 ... -0.00243592 -0.00543096
 -0.00993391]
[-0.01049267  0.007394    0.00557588 ... -0.0016477  -0.00831988
 -0.00854111]
[ 0.01013531 -0.00607982 -0.00943135 ...  0.0098716  -0.0048932
  0.00583843]
[ 0.00488947  0.011262   -0.00777578 ...  0.00451307 -0.00580831
 -0.00555568]
[ 0.          0.          0.         ... -0.00908671  0.0053047
  0.00792719]
[ 0.00916868  0.00768917 -0.00569182 ... -0.00555069 -0.01341268
 -0.01382084]
[-0.00325541  0.00873311 -0.00214143 ... -0.00284365  0.0070977
 -0.0028934 ]


[ 0.00331834  0.00694353 -0.00692774 ...  0.          0.
  0.        ]
[-0.01391783 -0.00689527  0.0111341  ...  0.          0.
  0.        ]
[ 0.          0.          0.         ...  0.00222733 -0.00650705
 -0.00509201]
[ 0.          0.          0.         ... -0.00800599  0.0118344
  0.00406735]
[ 0.01315044 -0.02525559  0.00211414 ...  0.          0.
  0.        ]
[ 0.00532015 -0.00181514 -0.00412952 ...  0.00890467 -0.00478222
  0.01193266]
[ 0.00728948 -0.0057027  -0.00595301 ...  0.          0.
  0.        ]
[ 0.01515205 -0.01267706  0.01334308 ...  0.00379583 -0.00617743
 -0.00888035]
[-0.00874874 -0.00625132  0.00347401 ...  0.00161842 -0.00122855
 -0.00145256]
[ 0.01019669  0.01197133 -0.01613508 ...  0.          0.
  0.        ]
[ 0.00764752  0.00978643 -0.01045498 ... -0.01009464  0.0087152
  0.00828747]
[ 0.          0.          0.         ... -0.01452047  0.01285523
  0.01408973]
[-0.0256419   0.01255547  0.02085281 ...  0.00712607  0.00664114
  0.00427119]
[ 0.00885364  0

[-0.01218817 -0.00596978 -0.00482352 ...  0.00369931 -0.0106926
 -0.01025559]
[ 0.00426422  0.00120854 -0.005267   ...  0.00312048  0.00692801
  0.00644925]
[ 0.          0.          0.         ... -0.0042145  -0.00423888
 -0.00548391]
[ 0.00423129  0.0043788  -0.00842773 ...  0.00326042 -0.0038503
 -0.00517684]
[ 0.          0.          0.         ... -0.01165797 -0.00415575
  0.00775398]
[-0.00756001 -0.00437328  0.00690589 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ... -0.0167083   0.01191823
  0.01483053]
[ 0.0033145   0.00134269 -0.00528603 ...  0.01013241 -0.0065648
  0.00706165]
[ 0.          0.          0.         ... -0.00163218 -0.00886599
 -0.01100238]
[-0.00648687  0.00568368 -0.00553533 ... -0.00408163 -0.00430476
 -0.00668506]
[ 0.00552003 -0.0059647  -0.00363967 ... -0.00764504  0.01056439
  0.00847615]
[ 0.01113111 -0.00828168 -0.00620827 ...  0.00754959 -0.00605098
  0.00509676]
[ 0.          0.          0.         ... -0.009657    0.0038573

[-0.00737317  0.00962715  0.00603941 ...  0.00142347 -0.0051571
 -0.00424163]
[-0.01255933 -0.00627964  0.00928462 ... -0.00452541 -0.00635376
 -0.00495527]
[ 0.          0.          0.         ...  0.00320435 -0.00129506
 -0.00513425]
[-0.00791716  0.00166908  0.00342963 ...  0.00896716 -0.01334577
 -0.00796199]
[-0.01394304 -0.01870033 -0.0128576  ... -0.00629602  0.00522411
  0.00222786]
[-0.00651543 -0.0025915  -0.00311905 ... -0.00419674 -0.00271875
 -0.00666439]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[ 0.0035559   0.00411089 -0.00634038 ...  0.00149329 -0.01017614
 -0.00917876]
[ 0.00549638 -0.0055425  -0.01374173 ...  0.          0.
  0.        ]
[-0.01655462  0.00818175  0.01524457 ...  0.00633675 -0.01055431
 -0.01038204]
[-0.01084376 -0.00340128 -0.01711296 ...  0.          0.
  0.        ]
[ 0.0069537  -0.00459271  0.00463723 ...  0.00373044 -0.00651278
 -0.00784465]
[ 0.00535059  0.00470233 -0.00543878 ...  0.          0.
  0.        ]
[-0.01011531  0.00751416  0.0

...

[ 0.01330894  0.01109258  0.00727012 ... -0.01401908  0.01866375
  0.00988727]
[ 0.00754953 -0.0099029  -0.00367697 ...  0.00698545  0.0083102
  0.01163622]
[ 0.          0.          0.         ... -0.00390358  0.00765368
  0.00974847]
[-0.0090657   0.01658581 -0.00398538 ...  0.00562161 -0.00553909
 -0.00908361]
[ 0.          0.          0.         ...  0.00856107 -0.02358197
 -0.02326545]
[-0.01240486 -0.00889151  0.00310919 ... -0.00314023 -0.00769654
 -0.00710514]
[ 0.          0.          0.         ...  0.00536873  0.00388134
 -0.00283431]
[ 0.0014131   0.00284042 -0.00872427 ...  0.00882019  0.00655092
  0.00614254]
[ 0.00515794  0.00842432 -0.01312413 ...  0.01001517  0.00603911
 -0.00483002]
[-0.00223802  0.00545227 -0.00437642 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ...  0.01188812 -0.00877924
  0.01171398]
[0. 0. 0. ... 0. 0. 0.]
[ 0.01884666  0.00741159  0.00144257 ... -0.00319167 -0.00408276
 -0.00436186]
[ 0.00203079  0.00392393 -0.0073197  

[ 0.00511049  0.00502816 -0.00722689 ...  0.00531226 -0.01601506
 -0.01581831]
[-0.01170557  0.00746742 -0.01013666 ... -0.00623753  0.0087471
  0.00270646]
[ 0.00550405 -0.00316588 -0.00192723 ... -0.01072602  0.00282929
  0.00686302]
[-0.01302989  0.01114053 -0.00608594 ...  0.00291198 -0.00769899
 -0.00736138]
[ 0.01763788  0.0103508   0.01616944 ...  0.00366576 -0.00730625
 -0.01075749]
[ 0.00294438  0.00862367 -0.01482183 ...  0.          0.
  0.        ]
[ 0.01609293  0.01350679  0.00827378 ... -0.00868942  0.00752858
  0.00434668]
[-0.00622297 -0.00744926 -0.00656191 ... -0.0022282  -0.00824317
  0.00631072]
[ 0.          0.          0.         ...  0.00081745 -0.00077146
 -0.0043844 ]
[ 0.00431763 -0.00093019 -0.00551305 ... -0.00650759  0.01513665
  0.00971566]
[0. 0. 0. ... 0. 0. 0.]
[0.         0.         0.         ... 0.00585503 0.00880836 0.00719278]
[ 0.          0.          0.         ...  0.00373382 -0.01089665
 -0.01136068]
[0.         0.         0.         ... 0.0119

[ 0.00391803  0.00572873 -0.0109722  ... -0.00770409 -0.00765065
 -0.00431061]
[0. 0. 0. ... 0. 0. 0.]
[-0.00986297 -0.0101054   0.00612789 ... -0.00699867  0.00500199
  0.00576   ]
[-0.01255014  0.00527252  0.01197976 ...  0.00614704 -0.00450497
 -0.00672771]
[-0.01204719 -0.00360884  0.00482449 ... -0.00640502 -0.00381091
  0.00418533]
[ 0.01681884 -0.00094798  0.01159945 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ... -0.00236114 -0.00099262
 -0.00495795]
[ 0.00515323  0.00666974 -0.01180395 ...  0.00340972 -0.00510002
 -0.00577221]
[ 0.00121449  0.00834286 -0.00589558 ...  0.          0.
  0.        ]
[-0.00218728  0.00569542 -0.00782943 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ... -0.00181232 -0.02149763
 -0.01957917]
[ 0.          0.          0.         ... -0.00395448 -0.00576005
 -0.00399349]
[ 0.00843925 -0.00951642  0.00575805 ...  0.          0.
  0.        ]
[-0.01892697 -0.01016901  0.01292478 ... -0.00076997 -0.0069

[ 0.004742    0.00528738 -0.00730937 ...  0.006326   -0.00563824
 -0.0060524 ]
[-0.00961621 -0.00632317  0.00713201 ...  0.          0.
  0.        ]
[-0.01693948  0.01044636  0.01222964 ... -0.0097216   0.01206727
  0.00877821]
[ 0.0064411  -0.00342629 -0.00191819 ...  0.00446206 -0.00537898
 -0.0055428 ]
[ 0.          0.          0.         ...  0.00525982 -0.00571681
 -0.00594537]
[ 0.01116981 -0.00113737 -0.00787908 ...  0.          0.
  0.        ]
[ 0.0095839   0.00574057  0.00736159 ...  0.00249908 -0.0022205
 -0.00490656]
[ 0.01182991 -0.00251552  0.01110987 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ... -0.00620373 -0.00519698
 -0.00434275]
[ 0.00460554  0.01359569 -0.00647683 ...  0.          0.
  0.        ]
[-0.00250196  0.00195566 -0.00390427 ... -0.00886967  0.00511293
  0.00772087]
[-0.00178981 -0.00794099 -0.01225147 ... -0.00316558 -0.00849083
 -0.00802973]
[-0.03015363 -0.00354672  0.02408941 ...  0.          0.
  0.        ]
[ 0.          

[ 0.          0.          0.         ...  0.00362443 -0.01095812
 -0.01064849]
[-0.00682556 -0.00599802  0.00742748 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ... -0.00864074  0.00654297
  0.00809897]
[0. 0. 0. ... 0. 0. 0.]
[-0.00703004  0.00468866 -0.0027162  ...  0.00755139 -0.0094484
 -0.00874587]
[-0.0111554   0.00728257 -0.01182755 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ... -0.00237463  0.01277269
  0.00248463]
[ 0.01136783 -0.01222496 -0.00678548 ...  0.          0.
  0.        ]
[-0.02965105 -0.02186715  0.00103746 ...  0.00205813 -0.01628991
 -0.01542775]
[ 0.          0.          0.         ... -0.00365756 -0.00314842
 -0.0062973 ]
[ 0.00392665 -0.00251054  0.00765701 ... -0.00426773 -0.00673918
 -0.00658933]
[ 0.00939734  0.01232159 -0.012535   ...  0.00932714  0.01023326
 -0.0075972 ]
[-0.01087834  0.01495675  0.00779008 ...  0.          0.
  0.        ]
[ 0.          0.          0.         ...  0.00281478 -0.01117

In [88]:
clf = cv2.ml.KNearest_create()
clf.train(np.float32(vlad_des), cv2.ml.ROW_SAMPLE, np.float32(labels))


True

In [89]:
ret, results, neighbours ,dist = clf.findNearest(np.float32(vlad_des_test), k=10)

In [90]:
print (results)
print (labels_test)

[[6.]
 [0.]
 [8.]
 ...
 [3.]
 [1.]
 [7.]]
[array([3]), array([8]), array([8]), array([0]), array([6]), array([6]), array([1]), array([6]), array([3]), array([1]), array([0]), array([9]), array([5]), array([7]), array([9]), array([8]), array([5]), array([7]), array([8]), array([6]), array([7]), array([0]), array([4]), array([9]), array([5]), array([2]), array([4]), array([0]), array([9]), array([6]), array([6]), array([5]), array([4]), array([5]), array([9]), array([2]), array([4]), array([1]), array([9]), array([5]), array([4]), array([6]), array([5]), array([6]), array([0]), array([9]), array([3]), array([9]), array([7]), array([6]), array([9]), array([8]), array([0]), array([3]), array([8]), array([8]), array([7]), array([7]), array([4]), array([6]), array([7]), array([3]), array([6]), array([3]), array([6]), array([2]), array([1]), array([2]), array([3]), array([7]), array([2]), array([6]), array([8]), array([8]), array([0]), array([2]), array([9]), array([3]), array([3]), array([8]

In [91]:
pred_label = []


for labels in labels_test:
    for label in labels:
        pred_label.append(label)
        
result_list = []
for result in results :
    for i in result:
        result_list.append(int(i))

# print (result_list)
# print (pred_label)
    
accuracy_score(results, pred_label)

0.3228

In [78]:
print(sift_des.shape)

(4546575, 64)
